In [1]:
import warnings
warnings.filterwarnings('ignore')

import pandas as pd
import numpy as np
import os
import shutil
import sys
import timeit
import tensorflow.keras.backend as K
from collections import deque
import threading
import pickle
from dcfs.dcfs import DCFS
import multiprocessing as mp


from sklearn.model_selection import cross_val_score
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import ExtraTreesClassifier
from sklearn import metrics


import tensorflow


2023-11-23 12:09:14.347522: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-11-23 12:09:14.352952: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-11-23 12:09:14.352964: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn import tree
from sklearn.naive_bayes import MultinomialNB
from tensorflow.keras.utils import to_categorical
from sklearn.preprocessing import StandardScaler

class Enviorement:

    def __init__(self, location, file_name, number_of_clusters, learner_model):
        self.data = pd.read_csv(location + '/' + file_name)
        self.data = self.state_scaler(self.data)
        self.action_space = number_of_clusters
        self.data_size = len(self.data)
        self.learner_model = learner_model
        
    def state_scaler(self, dataset):
        print(dataset.head())
        X = dataset.iloc[:, 0:dataset.shape[1] - 1]  # all rows, all the features and no labels
        y = dataset.iloc[:, -1]
        scaler = StandardScaler() 
        dataset2 = pd.concat([pd.DataFrame(scaler.fit_transform(X), columns=X.columns), y], axis = 1)
        print(dataset2.head())
        return dataset2
        
    def get_sample_data(self, dataset, sample_size):
        sample_data = dataset.sample(frac=sample_size, replace=False, random_state=1)
        return sample_data
    
    def data_separate(self, dataset):
        global X
        global y
        X = dataset.iloc[:, 0:dataset.shape[1] - 1]  # all rows, all the features and no labels
        y = dataset.iloc[:, -1]  # all rows, label only
        return X, y

    def learner_predict(self, row, learner, features):
        if learner == 'n/a':
            return 0 
        else:
            row = row.iloc[0:len(row)-3]
            x = row.iloc[0:len(row)-1].iloc[features]
            x = np.array(x).reshape(-1, len(features)) # all rows, all the features and no labels
            y = row.iloc[-1] 
            y_pred = learner.predict(x)
            y_pred_prob = learner.predict_proba(x)       
            y_pred_prob = y_pred_prob.max(axis=1)
            accuracy = 1.0  * (y == y_pred) * y_pred_prob
            return accuracy[0]
        
    def leraner(self, X_train, y_train):
        if self.learner_model == 'DT':
            learner = tree.DecisionTreeClassifier(max_depth=5)
            learner = learner.fit(X_train, y_train)
        
        y_pred = learner.predict(X_train)
        y_pred_prob = learner.predict_proba(X_train)       
        accuracy_socre = metrics.balanced_accuracy_score(y_train, y_pred)
        print(f"accuracy_socre {accuracy_socre}")
        return accuracy_socre, learner
    
#     def leraner(self, X_train, X_test, y_train, y_test):
#         if self.learner_model == 'DT':
#             learner = tree.DecisionTreeClassifier(max_depth=5)
#             learner = learner.fit(X_train, y_train)
#             y_pred = learner.predict(X_test)
#             y_pred_prob = learner.predict_proba(X_test)

#         elif self.learner_model == 'NB':
#             learner = MultinomialNB()
#             learner = learner.fit(X_train, y_train)
#             y_pred = learner.predict(X_test)
#             y_pred_prob = learner.predict_proba(X_test)
    

#         accuracy_socre = metrics.balanced_accuracy_score(y_test, y_pred)
        
#         print(f"accuracy_socre {accuracy_socre}")
#         y_pred_prob = y_pred_prob.max(axis=1)
#         accuracy = 1.0  * (y_test == y_pred) * y_pred_prob
#         return accuracy, accuracy_socre


In [3]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import load_model, Sequential
from tensorflow.keras.layers import Input, Dense, Dropout, Activation, BatchNormalization, MaxPooling2D, LSTM, Flatten, Lambda, Subtract, Multiply, Add, concatenate, GRU
from tensorflow.keras.optimizers import SGD, Adam, RMSprop, Nadam
from tensorflow.keras.callbacks import CSVLogger
from tensorflow.keras.models import Model



class Agent:
    def __init__(self, env):
        self.csv_logger = CSVLogger('log.csv', append=True, separator=';')
        self.env = env
        self.input_dim = env.data.shape[1] - 1
        self.output_dim = env.action_space
            
        self.q_model = self.create_Q_model() 
        self.full_model=self.create_full_model()
        
        
    def create_Q_model(self): #VarianceScaling #kernel_initializer='RandomUniform'
        x = Input((self.input_dim,))
        layer1 = Dense(100, activation='relu', name='layer1')(x)
#         layer2 = Dense(20 , activation='relu', name='layer2')(layer1)
#         layer3 = Dense(20, activation='relu', name='layer3')(layer2)
        output = Dense(self.output_dim, activation='sigmoid', name='output')(layer1) # Ones
#         output = Dense(self.output_dim, activation='softmax', name='output')(layer1) # Ones

#         output = Dense(self.output_dim, activation='linear', name='output')(layer1) # Ones
        model = Model(x, output)
        return model

    def create_full_model(self):
        input_state = Input(self.input_dim)
        action_id = Input(shape=[1], dtype='uint8')
        predicted_Qvalues = self.q_model(input_state)
        leave_only_action_value = tf.one_hot(action_id, self.output_dim)
        leave_only_action_value = tf.squeeze(leave_only_action_value, axis=1)
        predicted_q_for_action = tf.reduce_sum(predicted_Qvalues * leave_only_action_value, axis=1, keepdims=True)
        return Model([input_state, action_id], predicted_q_for_action)

    def complie(self, l_r):
        adam = Adam(lr=l_r)
        self.full_model.compile(loss='binary_crossentropy', metrics=['accuracy'], 
                           optimizer=adam) #logcosh
#         self.full_model.compile(loss='categorical_crossentropy', metrics=['accuracy'], 
#                            optimizer=adam) #logcosh
#         self.full_model.compile(loss='logcosh', metrics=['accuracy'], 
#                            optimizer=adam) #logcosh

    def act(self, state, eps):
        if np.random.rand() < eps:
            a = np.random.choice(self.output_dim, state.shape[0])

        else:
#             a = np.argmax(self.q_model.predict(state), axis=1)
#             tf.keras.backend.set_floatx('float64')
            a = np.argmax(self.q_model(state.to_numpy()).numpy(), axis=1)
        return a

    def train(self, X_batch, y_batch, batch_size):
#         print("model train")
        return self.full_model.fit(X_batch, y_batch, epochs=5, steps_per_epoch=1, batch_size=batch_size, verbose=0)


In [4]:
import numpy as np
import tensorflow as tf

class Genreal_func:
    def __init__(self):
        return

    def learningRate(self, epi, l_r_schedule, episodes):
        l_r = 0.0
        for episode_boundary, lr in l_r_schedule:
            if epi >= episodes * episode_boundary:
                l_r = lr
        print('epoch, lr: ', epi, l_r)
        return l_r

    def epsilon(self, epi, epsilon_schedule, episodes):
        eps = 0.0
        for episode_boundary, epsilon in epsilon_schedule:
            if epi >= episodes * episode_boundary:
                eps = epsilon
        print('epoch, epsilon: ', epi, eps)
        return eps

In [5]:
import numpy as np
from collections import deque
# from dcc.dcc_general_functions import Genreal_func

class RunProcess():

    def __init__(self, param, dcfs_per_cluster,env, agent):
        self.DCFS_discount_rate = param.DCFS_discount_rate
        self.DCFS_episode_size = param.DCFS_episode_size
        self.DCFS_in_iter = param.DCFS_in_iter
        self.DCFS_l_r_schedule = param.DCFS_l_r_schedule
        self.DCFS_epsilon_schedule = param.DCFS_epsilon_schedule
        self.number_of_clusters = param.number_of_clusters
        self.sample_size = param.sample_size
        self.dcfs_per_cluster = dcfs_per_cluster
        self.env = env
        self.agent = agent 

        return
    
    def sigmoid(self, x):
        return 1.0 / (1.0 + np.exp(-x))

    def main_process(self,eps, epi, episodes):
        genreal_func = Genreal_func()

    #     states, y  = env.data_separate(env.data) # TODO: Replace with data sample and not all data
        sample_data = self.env.get_sample_data(self.env.data, sample_size=self.sample_size)
        states, y  = self.env.data_separate(sample_data)
        print(f"episode data size shape {states.shape[0]}")

        a = self.agent.act(states, eps)
        print(sum(a))
        DCFS_eps=genreal_func.epsilon(epi, self.DCFS_epsilon_schedule, episodes)
        print (f"DCFS_eps {DCFS_eps}")
        DCFS_l_r=genreal_func.learningRate(epi, self.DCFS_l_r_schedule, episodes)  
        print (f"DCFS_l_r {DCFS_l_r}")

    #     full_data = env.data.copy()
        full_data = sample_data.copy()
        full_data["cluster_id"] = a
        full_data["reward"] = -100
        full_data["index"]=full_data.index

        r = np.copy(a)
        learner_cluster_accuracy_list = []

        ## get features and learner for each cluster 
        leraner_dict = {}
        feature_dict = {}
        for i in range(self.number_of_clusters):

            # get data for each cluster
            cluster_data = full_data[full_data.cluster_id==i]
            cluster_data = cluster_data.iloc[:, 0:cluster_data.shape[1] - 3]

            if cluster_data.shape[0]>10:
                print(f"start dcfs for cluster {i}")
                features = self.dcfs_per_cluster[i].run_dcfs(cluster_data, self.DCFS_in_iter, DCFS_l_r, DCFS_eps,
                                                        episode_size=min(cluster_data.shape[0]-1,self.DCFS_episode_size))
                features = features[0:-1]
                feature_dict[i] = features
                print(f"features for cluster {i} are {features}")
                
                if len(features)>0:
                    x, y  = env.data_separate(cluster_data)
                    x = x.iloc[:, features]
                    cluster_accuracy_socre, lear = env.leraner(x, y)
                    leraner_dict[i] = lear 
                    learner_cluster_accuracy_list.append(cluster_accuracy_socre)
                else:
                    leraner_dict[i] = 'n/a'                
                    
        # get rearwd for each row 
        d = {}
        for i in range(self.number_of_clusters):
            d[i] = np.delete(np.arange(self.number_of_clusters), i)

        if len(feature_dict) !=self.number_of_clusters:
            print(f"update full data")
            full_data = full_data[full_data.cluster_id.isin(list(feature_dict.keys()))]
            states = full_data.iloc[:, 0:full_data.shape[1] - 4] 
            a = full_data['cluster_id']
            
        cluster_reward = list(full_data.apply(lambda x: env.learner_predict(x, leraner_dict[x.cluster_id], 
                                                                            feature_dict[x.cluster_id]), axis = 1))
        
        if len(feature_dict) !=self.number_of_clusters:
            full_data['reward'] =  self.sigmoid(np.array(cluster_reward))
        else:
            other_reward = []
            for j in range(self.number_of_clusters-1):
                other_reward.append(list(full_data.apply(lambda x: env.learner_predict(x, leraner_dict[d[x.cluster_id][j]],
                                                                                   feature_dict[d[x.cluster_id][j]]), axis = 1)))
    
            full_data['reward'] =  self.sigmoid(cluster_reward - np.array(other_reward).max(axis=0))
        
        r = full_data["reward"]
        print(f"r {r}")


        if len(learner_cluster_accuracy_list)>0:
            mean_cluster_accuracy_socre = np.min(learner_cluster_accuracy_list)
        else:
            mean_cluster_accuracy_socre = 0 
        return states, a, r, mean_cluster_accuracy_socre

In [6]:
class actorthread(threading.Thread):
    def __init__(self,thread_id,threadLock, eps):
        threading.Thread.__init__(self)
        self.thread_id = thread_id
        self.eps = eps
        self.threadLock = threadLock
        
    def run(self, epi, episodes):

        self.threadLock.acquire()
    
        print(f"therad {self.thread_id}")
        states, a, r , mean_cluster_accuracy_socre = run_process.main_process(self.eps, epi, episodes)
        
        self.threadLock.release()

        return  states, a, r, mean_cluster_accuracy_socre

In [7]:
#parameters
class Param():
    Q_model = '1 layer 100'
    number_of_experiment=5
    file = 'no_show_sample' #tmdb_5000_movies
    experiment_name = f"2{file}_with_exploration_scale_new_reward_sigmoid_on_reward_200_1000"
    number_of_clusters = 2
    learner_model ='DT'
    
    l_r_schedule = [(0, 0.1), (0.05, 0.01), (0.1, 0.005), (0.15, 0.001)]
    epsilon_schedule = [(0, 0.9), (0.05, 0.5), (0.1, 0.3), (0.15, 0.001)]
#     l_r_schedule = [(0, 0.001)]
#     epsilon_schedule = [(0, 0.001)]

    episodes= 1000
    threads = 1
    sample_size = 1
    
    experiment_name = f"{experiment_name}_{sample_size}_{number_of_clusters}"

    location = "datasets"
    file_name= f"{file}_train_data.csv" #'toy_small_with_test_train.csv'
    test_file = f"{file}_test_data.csv"

    # DCFS parameters 
    DCFS_discount_rate=0
    DCFS_episode_size=200
    DCFS_in_iter = 3
    DCFS_l_r_schedule = [(0,0.1), (0.25, 0.01), (0.5, 0.005), (0.75, 0.001)]
    DCFS_epsilon_schedule = [(0,0.9), (0.25, 0.5), (0.5, 0.3), (0.75, 0.001)]
#     DCFS_epsilon_schedule = [(0,0.9), (0.5, 0.01)]

#     DCFS_epsilon_schedule = [(0,0.99), (0.25, 0.01)]

In [8]:
param = Param()

In [9]:
# Main experiments folder management: 
if not os.path.exists('Experiments/'+ str(param.experiment_name)):
    os.makedirs('Experiments/'+ str(param.experiment_name))
else:
    shutil.rmtree('Experiments/'+ str(param.experiment_name))        
    os.makedirs('Experiments/'+ str(param.experiment_name))

In [10]:
file = open(f'Experiments/{str(param.experiment_name)}/parameters.txt', 'w')

file.write(f'file_name {param.file_name} \n')
file.write(f'number_of_clusters {param.number_of_clusters}\n')
file.write(f'learner_model {param.learner_model}\n')
file.write(f'DCFS_discount_rate {param.DCFS_discount_rate}\n')
file.write(f'DCFS_episode_size {param.DCFS_episode_size}\n')
file.write(f'DCFS_l_r_schedule {param.DCFS_l_r_schedule}\n')
file.write(f'DCFS_epsilon_schedule {param.DCFS_epsilon_schedule}\n')
file.write(f'DCFS_in_iter {param.DCFS_in_iter}\n')
file.write(f'number_of_experiment {param.number_of_experiment}\n')
file.write(f'epsilon_schedule {param.epsilon_schedule}\n')
file.write(f'l_r_schedule {param.l_r_schedule}\n')
file.write(f'episodes {param.episodes}\n')
file.write(f'Q_model {param.Q_model}\n')
# file.write(f'stop_thrashold {stop_thrashold}\n')
file.write(f'sample_size {param.sample_size}\n')
file.write(f'threads {param.threads}\n')

file.close()

### Run experiment

In [11]:
K.clear_session()

for e in range (param.number_of_experiment):
    
    # set experiment folder: 
    if not os.path.exists(f'Experiments/{param.experiment_name}/exp_{e}'):
        os.makedirs(f'Experiments/{param.experiment_name}/exp_{e}')
    else:
        shutil.rmtree(f'Experiments/{param.experiment_name}/exp_{e}')        
        os.makedirs(f'Experiments/{param.experiment_name}/exp_{e}')

    
    d = {}
    start = timeit.default_timer()
    print ('Experiments ' + str(e) + ' start')

    # initate classes 
    env = Enviorement(param.location, param.file_name, param.number_of_clusters, param.learner_model)
    agent = Agent(env)
    dcfs_per_cluster = [DCFS(number_of_features_in_data=env.data.shape[1]-1, 
                             discount_rate=param.DCFS_discount_rate,print_log=False) for i in range(param.number_of_clusters)]
    run_process = RunProcess(param, dcfs_per_cluster,env, agent)
    genreal_func = Genreal_func()

    
    
    current_lr = param.l_r_schedule[0][1]
    agent.complie(current_lr)
    
    accuracy_list = []
    cluster_accuracy_socre_list = []
    epi_episodes = int(param.episodes/param.threads)
    
#     ### check cluater accuracy - relevant only for toy data 
#     states, y  = env.data_separate(env.data)
#     a = agent.act(states, 0)
#     accuracy = np.sum(a == np.concatenate ([np.full(int(env.data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))/int(env.data.shape[0])
#     print(f"clustering accuracy = {accuracy}") 
#     accuracy_list.append(accuracy)    
        
    print(f"number of episodes {epi_episodes}")
    for epi in range(epi_episodes):
        episode_start = timeit.default_timer()
        print('episode {} start'.format(epi))
        

        
        
#         if epi>0 and (cluster_accuracy_socre_list[-1])>=stop_thrashold:
#             l_r_schedule = [(0,0.001)]
#             epsilon_schedule = [(0,0.001)]
            
        l_r=genreal_func.learningRate(epi, param.l_r_schedule, epi_episodes)
        eps=genreal_func.epsilon(epi, param.epsilon_schedule, epi_episodes)
                                
        if l_r != current_lr:
            print("complie model")
            agent.complie(l_r)
            current_lr = l_r

         
        threadLock = threading.Lock()

        jobs = []
        states_list = []
        a_list =[]
        r_list = []
        socre_list = []
        
        for i in range(param.threads): 
            thread = actorthread(i, threadLock, eps)
            jobs.append(thread)

        for j in jobs:
            t_states, a, r, mean_cluster_accuracy_socre  =  j.run(epi, epi_episodes)
            states_list.append(t_states)
            a_list.append(a)
            r_list.append(r)
            socre_list.append(mean_cluster_accuracy_socre)
            
        
        
        t_states = pd.concat(states_list, axis=0)
        a = [item for sublist in a_list for item in sublist]
        r = pd.concat(r_list, axis=0)  
        
        agent.train([t_states.to_numpy(),np.array(a)],np.array(r), batch_size=32)        
        
        socre = np.min(socre_list)
        cluster_accuracy_socre_list.append(socre)

        ### check cluater accuracy - relevant only for toy data 
        states, y  = env.data_separate(env.data)
        a = agent.act(states, 0)
        if len(a) % 2 == 0: 
            accuracy = np.sum(a == np.concatenate ([np.full(round(env.data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))/int(env.data.shape[0])
        else:
            accuracy = np.sum(np.append(a,0) == np.concatenate ([np.full(round(env.data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))/int(env.data.shape[0])

    
        print(f"clustering accuracy = {accuracy}") 
        accuracy_list.append(accuracy)
        
        ### cluster_accuracy_socre_list
        print(f"cluster learner accuracy {cluster_accuracy_socre_list[-1]}")
    
    ## final feature list 
    states, y  = env.data_separate(env.data)
    a = agent.act(states, 0)
    print(a)        
    full_data = env.data.copy()
    full_data["cluster_id"] = a
    full_data["reward"] = -100
    full_data["index"]=full_data.index

    feature_selection = {}
    for i in range(param.number_of_clusters):

        # get data for each cluster
        cluster_data = full_data[full_data.cluster_id==i]
        cluster_data = cluster_data.iloc[:, 0:cluster_data.shape[1] - 3]
        
        if cluster_data.shape[0] < 5:
            print(f"No cluster {i}")
            features = 'n/a'
        else:
            features = dcfs_per_cluster[i].run_dcfs(cluster_data, 1, 0.0001, 0, episode_size=cluster_data.shape[0])
            features = features[0:-1]
            print(f"features for cluster {i} are {features}")
        feature_selection[i] = features          
        
    ### check cluater accuracy - relevant only for toy data 
    if len(a) % 2 == 0: 
        accuracy = np.sum(a == np.concatenate ([np.full(int(full_data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))//int(full_data.shape[0])
    else:
        accuracy = np.sum(np.append(a,0)  == np.concatenate ([np.full(int(full_data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))//int(full_data.shape[0])

    print(f"clustering accuracy = {accuracy}") # TODO replace with actual reward 
    end = timeit.default_timer()
    exp_runtime = end - start 
    print(f"experiment time {exp_runtime}")
    
    #### Results
    d['accuracy_list']= accuracy_list
    d['cluster_accuracy_socre_list']=cluster_accuracy_socre_list 
    d["runtime"] = exp_runtime

    ### cluster  Test accuracy 
    test_env = Enviorement(param.location, param.test_file , param.number_of_clusters, param.learner_model)
    test_states, test_y  = test_env.data_separate(test_env.data)
    test_a = agent.act(test_states, 0.0)
    print(test_a)        

    if len(test_a) % 2 == 0: 
        test_accuracy = np.sum(test_a == np.concatenate ([np.full(int(test_env.data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))/int(test_env.data.shape[0])
    else:
        test_accuracy = np.sum(np.append(test_a,0) == np.concatenate ([np.full(int(test_env.data.shape[0]/param.number_of_clusters), i) for i in range(param.number_of_clusters)]))/int(test_env.data.shape[0])

    
    print(f'test_cluster_accuracy {test_accuracy}')
    print(f'train_cluster_accuracy {accuracy}')

    d['feature_selection'] = feature_selection
    d['train_cluster_accuracy'] =  accuracy
    d['test_cluster_accuracy'] = test_accuracy
    
    for i in range(param.number_of_clusters): 
        d[f'train_cluster_{i}_size'] = len(a[a==i])
        d[f'test_cluster_{i}_size'] = len(test_a[test_a==i])
    ### train/test classification accuracy 

#     learner = GradientBoostingClassifier(random_state=0)
    learner = GradientBoostingClassifier(random_state=0, max_depth=3, n_estimators=50)
    d['learner'] = learner

    # train:
    train_states, train_y  = env.data_separate(env.data)

    accuracy = round(cross_val_score(learner, train_states, train_y, scoring='balanced_accuracy' , cv=3).mean(),3)
    print(f"accuracy_classifiction_train_socre {accuracy}")
    d[f"train_classifiction_accuracy_socre"] = accuracy

    full_data = env.data.copy()
    full_data["cluster_id"] = a

    # get data for each cluster
    for i in range(param.number_of_clusters): 
        cluster_data = full_data[full_data.cluster_id==i]
        cluster_data = cluster_data.iloc[:, 0:cluster_data.shape[1] - 1]
        feat =  feature_selection[i]

        if feat == 'n/a' or len(cluster_data)<5:
            print(f"cluster_{i}_train_classifiction_accuracy_socre n/a")
            d[f'cluster_{i}_train_classifiction_accuracy_socre'] = 0
        else:               
            x = cluster_data.iloc[:, feat]
            y = cluster_data.iloc[:, - 1]
            accuracy = round(cross_val_score(learner, x, y, scoring='balanced_accuracy' , cv=3).mean(),3)
            print(f"cluster_{i}_train_classifiction_accuracy_socre {accuracy}")
            d[f"cluster_{i}_train_classifiction_accuracy_socre"] = accuracy

    # test:


    train_states, train_y  = env.data_separate(env.data)
    test_states, test_y  = test_env.data_separate(test_env.data)

    learner = learner.fit(train_states, train_y)
    y_pred = learner.predict(test_states)

    accuracy_socre = metrics.balanced_accuracy_score(test_y, y_pred)
    print(f"test_classifiction_accuracy_socre {accuracy_socre}")
    d['test_classifiction_accuracy_socre'] = accuracy_socre

    full_data_train = env.data.copy()
    full_data_train["cluster_id"] = a

    full_data_test = test_env.data.copy()
    full_data_test["cluster_id"] = agent.act(test_states, 0.0)

    # get data for each cluster
    for i in range(param.number_of_clusters): 
        train_cluster_data = full_data[full_data_train.cluster_id==i]
        train_cluster_data = train_cluster_data.iloc[:, 0:train_cluster_data.shape[1] - 1]

        test_cluster_data = full_data_test[full_data_test.cluster_id==i]
        test_cluster_data = test_cluster_data.iloc[:, 0:test_cluster_data.shape[1] - 1]

        feat =  feature_selection[i]

        if feat == 'n/a' or len(test_cluster_data)<5:
            print(f"cluster_{i}_classifiction_test_accuracy_socre n/a")
            d[f'cluster_{i}_classifiction_test_accuracy_socre'] = 0
        else:        
            x_train = train_cluster_data.iloc[:, feat]
            y_train = train_cluster_data.iloc[:, - 1]

            x_test = test_cluster_data.iloc[:, feat]
            y_test = test_cluster_data.iloc[:, - 1]

            learner = learner.fit(x_train, y_train)
            y_pred = learner.predict(x_test)
            accuracy_socre = metrics.balanced_accuracy_score(y_test, y_pred)
            print(f"cluster_{i}_classifiction_test_accuracy_socre {accuracy_socre}")
            d[f'cluster_{i}_classifiction_test_accuracy_socre'] = accuracy_socre

    
    
    ## save model
    agent.q_model.save(f'Experiments/{param.experiment_name}/exp_{e}')
    
    # save results
    file = open(f'Experiments/{param.experiment_name}/results_{e}.txt', 'w')
    file.write(str(d))
    file.close()
    
    K.clear_session()

Experiments 0 start
   Age  Gender  DayOfTheWeek  Diabetes  Alcoolism  HiperTension  Handcap  \
0    8       0             0         0          0             0        0   
1    7       1             5         0          0             0        0   
2   63       0             5         0          0             0        0   
3   23       0             4         0          0             0        1   
4   18       1             4         0          0             0        0   

   Smokes  Scholarship  Tuberculosis  Sms_Reminder  AwaitingTime  Show_Up  
0       0            1             0             0           209        0  
1       0            0             0             1           207        1  
2       0            0             0             0           212        1  
3       0            0             0             0           212        1  
4       0            0             0             1           207        0  
        Age    Gender  DayOfTheWeek  Diabetes  Alcoolism  HiperTens

2023-11-23 12:09:18.859881: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2023-11-23 12:09:18.859915: W tensorflow/stream_executor/cuda/cuda_driver.cc:269] failed call to cuInit: UNKNOWN ERROR (303)
2023-11-23 12:09:18.859939: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (mmoran1-tensorflow-colab-deployment-75bf6588f5-f8csk): /proc/driver/nvidia/version does not exist
2023-11-23 12:09:18.860357: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


number of episodes 1000
episode 0 start
epoch, lr:  0 0.1
epoch, epsilon:  0 0.9
therad 0
episode data size shape 960
484
epoch, epsilon:  0 0.9
DCFS_eps 0.9
epoch, lr:  0 0.1
DCFS_l_r 0.1
start dcfs for cluster 0
features for cluster 0 are [7, 6, 0, 1]
accuracy_socre 0.5808454740864581
start dcfs for cluster 1
features for cluster 1 are [11, 4, 7, 9, 10]
accuracy_socre 0.530724946695096
r 241    0.500000
851    0.502183
436    0.511903
386    0.676087
345    0.464973
         ...   
767    0.500000
72     0.502183
908    0.575183
235    0.509719
37     0.503350
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.4708333333333333
cluster learner accuracy 0.530724946695096
episode 1 start
epoch, lr:  1 0.1
epoch, epsilon:  1 0.9
therad 0
episode data size shape 960
474
epoch, epsilon:  1 0.9
DCFS_eps 0.9
epoch, lr:  1 0.1
DCFS_l_r 0.1
start dcfs for cluster 0
features for cluster 0 are [0, 3, 9, 7, 6, 4]
accuracy_socre 0.5845507561530098
start dcfs for cluster 1
features f

features for cluster 0 are [7, 11, 1, 2, 0, 5, 3, 9, 10]
accuracy_socre 0.6041497975708502
start dcfs for cluster 1
features for cluster 1 are [11, 1, 4, 9, 0, 8]
accuracy_socre 0.582798833819242
r 241    0.500000
851    0.310026
436    0.405409
386    0.350459
345    0.534547
         ...   
767    0.500000
72     0.551037
908    0.696200
235    0.473690
37     0.518751
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.5052083333333334
cluster learner accuracy 0.582798833819242
episode 13 start
epoch, lr:  13 0.1
epoch, epsilon:  13 0.9
therad 0
episode data size shape 960
493
epoch, epsilon:  13 0.9
DCFS_eps 0.9
epoch, lr:  13 0.1
DCFS_l_r 0.1
start dcfs for cluster 0
features for cluster 0 are [11, 2, 4, 1, 6, 3]
accuracy_socre 0.5934778745334992
start dcfs for cluster 1
features for cluster 1 are [8, 11, 1, 7, 9, 10, 3]
accuracy_socre 0.5596515255268965
r 241    0.500000
851    0.512389
436    0.549834
386    0.498132
345    0.453704
         ...   
767    0.500000


features for cluster 0 are [7, 5, 10, 9, 1, 4, 0, 2]
accuracy_socre 0.6080931744312026
start dcfs for cluster 1
features for cluster 1 are [0, 11, 7, 4, 8, 2]
accuracy_socre 0.6227308066083577
r 241    0.622459
851    0.637294
436    0.479179
386    0.637294
345    0.506538
         ...   
767    0.500000
72     0.637294
908    0.511975
235    0.467062
37     0.488345
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.5020833333333333
cluster learner accuracy 0.6080931744312026
episode 25 start
epoch, lr:  25 0.1
epoch, epsilon:  25 0.9
therad 0
episode data size shape 960
12
epoch, epsilon:  25 0.9
DCFS_eps 0.9
epoch, lr:  25 0.1
DCFS_l_r 0.1
start dcfs for cluster 0
features for cluster 0 are [7, 0, 2, 3, 8, 9]
accuracy_socre 0.547359876019335
start dcfs for cluster 1
features for cluster 1 are [9, 3, 2, 10, 5, 8]
accuracy_socre 0.7857142857142857
r 241    0.377541
851    0.649738
436    0.684111
386    0.697059
345    0.681054
         ...   
767    0.377541
72     0.

...

features for cluster 0 are [11]
accuracy_socre 0.6738193799104503
start dcfs for cluster 1
features for cluster 1 are [4, 7]
accuracy_socre 0.5
r 241    0.500000
851    0.511042
436    0.497155
386    0.465400
345    0.488958
         ...   
767    0.377541
72     0.488958
908    0.493056
235    0.676694
37     0.511042
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.51875
cluster learner accuracy 0.5
episode 951 start
epoch, lr:  951 0.001
epoch, epsilon:  951 0.001
therad 0
episode data size shape 960
740
epoch, epsilon:  951 0.001
DCFS_eps 0.001
epoch, lr:  951 0.001
DCFS_l_r 0.001
start dcfs for cluster 0
features for cluster 0 are [11, 6, 4, 9, 7]
accuracy_socre 0.6761363636363636
start dcfs for cluster 1
features for cluster 1 are [4, 7]
accuracy_socre 0.5
r 241    0.500000
851    0.510867
436    0.496980
386    0.465574
345    0.489133
         ...   
767    0.377541
72     0.489133
908    0.493056
235    0.676541
37     0.510867
Name: reward, Length: 960, dtyp

r 241    0.500000
851    0.552033
436    0.515346
386    0.322280
345    0.519613
         ...   
767    0.377541
72     0.572443
908    0.628623
235    0.691618
37     0.655095
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.521875
cluster learner accuracy 0.5341350130432017
episode 963 start
epoch, lr:  963 0.001
epoch, epsilon:  963 0.001
therad 0
episode data size shape 960
699
epoch, epsilon:  963 0.001
DCFS_eps 0.001
epoch, lr:  963 0.001
DCFS_l_r 0.001
start dcfs for cluster 0
features for cluster 0 are [11, 6, 4, 9]
accuracy_socre 0.6771803037726605
start dcfs for cluster 1
features for cluster 1 are [7, 1, 11]
accuracy_socre 0.5337469292584419
r 241    0.500000
851    0.564676
436    0.515346
386    0.319556
345    0.512087
         ...   
767    0.377541
72     0.565052
908    0.628623
235    0.679968
37     0.661871
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.5197916666666667
cluster learner accuracy 0.5337469292584419
episode 964 star

features for cluster 0 are [11]
accuracy_socre 0.6714404317144043
start dcfs for cluster 1
features for cluster 1 are [7, 1, 11, 9]
accuracy_socre 0.5686429237885375
r 241    0.500000
851    0.553367
436    0.515346
386    0.316328
345    0.515664
         ...   
767    0.377541
72     0.591548
908    0.645656
235    0.683672
37     0.484336
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.515625
cluster learner accuracy 0.5686429237885375
episode 976 start
epoch, lr:  976 0.001
epoch, epsilon:  976 0.001
therad 0
episode data size shape 960
723
epoch, epsilon:  976 0.001
DCFS_eps 0.001
epoch, lr:  976 0.001
DCFS_l_r 0.001
start dcfs for cluster 0
features for cluster 0 are [11, 6]
accuracy_socre 0.6795474910394266
start dcfs for cluster 1
features for cluster 1 are [7, 11, 1]
accuracy_socre 0.5316132187655837
r 241    0.500000
851    0.543861
436    0.515346
386    0.325400
345    0.517910
         ...   
767    0.377541
72     0.517910
908    0.457494
235    0.691618

features for cluster 1 are [7, 11, 9]
accuracy_socre 0.5464810712847362
r 241    0.500000
851    0.479293
436    0.508533
386    0.453812
345    0.486381
         ...   
767    0.500000
72     0.520707
908    0.513619
235    0.684740
37     0.513619
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.5229166666666667
cluster learner accuracy 0.5464810712847362
episode 988 start
epoch, lr:  988 0.001
epoch, epsilon:  988 0.001
therad 0
episode data size shape 960
704
epoch, epsilon:  988 0.001
DCFS_eps 0.001
epoch, lr:  988 0.001
DCFS_l_r 0.001
start dcfs for cluster 0
features for cluster 0 are [11]
accuracy_socre 0.6733295259851514
start dcfs for cluster 1
features for cluster 1 are [7, 11]
accuracy_socre 0.5469872091231314
r 241    0.500000
851    0.512836
436    0.508533
386    0.315573
345    0.507032
         ...   
767    0.377541
72     0.556787
908    0.669340
235    0.684427
37     0.669340
Name: reward, Length: 960, dtype: float64
clustering accuracy = 0.521875


features for cluster 0 are [11, 6, 9]
features for cluster 1 are [7, 11]
clustering accuracy = 0
experiment time 4434.985904999077
   Age  Gender  DayOfTheWeek  Diabetes  Alcoolism  HiperTension  Handcap  \
0   68       0             4         0          0             0        0   
1   67       1             0         0          0             1        0   
2   14       1             1         0          0             0        0   
3   61       0             1         0          0             1        0   
4   52       0             5         0          0             1        0   

   Smokes  Scholarship  Tuberculosis  Sms_Reminder  AwaitingTime  Show_Up  
0       0            0             0             1           192        1  
1       0            0             0             0           211        1  
2       0            1             0             0           193        0  
3       0            0             0             0           206        1  
4       0            0          

In [12]:
# sum(a)

In [13]:
# print(list(env.data.Age_0_4_Poverty_Estimate))

In [14]:
# states

In [15]:
# data = pd.read_csv("datasets/census2_test_data.csv")

In [16]:
# data.iloc[:,3:].to_csv("datasets/census3_test_data.csv",index=False)

In [17]:
# data.iloc[0:-1,:].to_csv("datasets/adult_train_data.csv",index=False)

In [18]:
# data

In [19]:
# לנסות עם 3
# לשים את האבאלואציה גם בפונקציה

In [20]:
# from tensorflow import keras
# model = keras.models.load_model('Experiments')

In [22]:
param.number_of_experiment=5

results_df = pd.DataFrame(columns=['runtime'] + [f'feature_selection_{i}' for i in range(param.number_of_clusters)] + 
                                  [ 'train_classifiction_accuracy_socre'] +
                                  [f'cluster_{i}_train_classifiction_accuracy_socre' for i in range(param.number_of_clusters)] +
                                  [f'train_cluster_{i}_size' for i in range(param.number_of_clusters)] + 
                                  [ 'test_classifiction_accuracy_socre']+
                                  [f'cluster_{i}_classifiction_test_accuracy_socre' for i in range(param.number_of_clusters)] +
                                  [f'test_cluster_{i}_size' for i in range(param.number_of_clusters)] +                                                            
                                  ['accuracy_list','cluster_accuracy_socre_list'])


for i in range (param.number_of_experiment): 
    f = open(f'Experiments/{str(param.experiment_name)}/results_{i}.txt', 'r')
    data = f.read()
    data = eval(data)
    lista = [data['runtime']] + [data['feature_selection'][j] for j in range(param.number_of_clusters)] +[data['train_classifiction_accuracy_socre']] +  [data[f'cluster_{j}_train_classifiction_accuracy_socre'] for j in range(param.number_of_clusters)] +[data[f'train_cluster_{j}_size'] for j in range(param.number_of_clusters)] + [data['test_classifiction_accuracy_socre']] +[data[f'cluster_{j}_classifiction_test_accuracy_socre'] for j in range(param.number_of_clusters)] +[data[f'test_cluster_{j}_size'] for j in range(param.number_of_clusters)] + [data['accuracy_list'],data['cluster_accuracy_socre_list']]
    
    results_df.loc[len(results_df)] = lista

    f.close()

In [23]:
# results_df['AVG'] = ((results_df['cluster_0_classifiction_test_accuracy_socre']*results_df['test_cluster_0_size']) + (results_df['cluster_1_classifiction_test_accuracy_socre']*results_df['test_cluster_1_size']))/1300 

In [24]:
results_df

runtime feature_selection_0 feature_selection_1  \
0  4151.750253                 [7]                 n/a   
1  2739.339078              [8, 7]  [2, 0, 8, 7, 6, 9]   
2  4870.203853          [10, 3, 7]   [11, 10, 6, 4, 9]   
3  2746.187644                 n/a  [8, 7, 9, 6, 5, 3]   
4  4434.985905          [11, 6, 9]             [7, 11]   

   train_classifiction_accuracy_socre  \
0                                 0.5   
1                                 0.5   
2                                 0.5   
3                                 0.5   
4                                 0.5   

  cluster_0_train_classifiction_accuracy_socre  \
0                                        0.497   
1                                        0.513   
2                                        0.577   
3                                          n/a   
4                                        0.535   

  cluster_1_train_classifiction_accuracy_socre train_cluster_0_size  \
0                                          n/a                  960   
1                                        0.333                  955   
2                                        0.532                  387   
3                                        0.516                    0   
4                                        0.519                  252   

  train_cluster_1_size  test_classifiction_accuracy_socre  \
0                    0                           0.488024   
1                    5                           0.488024   
2                  573                           0.488024   
3                  960                           0.488024   
4                  708                           0.488024   

  cluster_0_classifiction_test_accuracy_socre  \
0                                         0.5   
1                                         0.5   
2                                    0.526107   
3                                         n/a   
4                                    0.517787   

  cluster_1_classifiction_test_accuracy_socre test_cluster_0_size  \
0                                         n/a                 240   
1                                         n/a                 238   
2                                    0.499863                 101   
3                                    0.494012                   0   
4                                    0.498806                  56   

  test_cluster_1_size                                      accuracy_list  \
0                   0  [0.4708333333333333, 0.509375, 0.4958333333333...   
1                   2  [0.5010416666666667, 0.49583333333333335, 0.5,...   
2                 139  [0.4625, 0.5291666666666667, 0.511458333333333...   
3                 240  [0.49895833333333334, 0.521875, 0.494791666666...   
4                 184  [0.528125, 0.4739583333333333, 0.471875, 0.503...   

                         cluster_accuracy_socre_list  
0  [0.530724946695096, 0.5845507561530098, 0.5240...  
1  [0.5416135712010194, 0.5832297204596124, 0.582...  
2  [0.538963963963964, 0.544283608685131, 0.51034...  
3  [0.5571332737030411, 0.5823189810048648, 0.602...  
4  [0.5788152610441767, 0.5120508934099012, 0.555...

In [ ]:
round((env.data.shape[0])/2) * 2

In [ ]:
len(a[:-1])

In [ ]:

from matplotlib import pyplot as plt
%matplotlib inline

fig, axs = plt.subplots(1, figsize = (8,5))

    
i =3
print(i)
axs.set_title(f'experiment {i}')
axs.plot(results_df.loc[i].accuracy_list, label='cluster_accuracy')
# axs.plot(results_df.loc[i].cluster_accuracy_socre_list, label='cluster_learner_accuracy')
axs.legend(loc='center right')

plt.show()



In [ ]:
plt.plot(results_df.loc[0].accuracy_list, label='cluster_accuracy')

In [ ]:
plt.plot(results_df.loc[i].cluster_accuracy_socre_list, label='cluster_learner_accuracy')

In [ ]:
print(list(a))